# Averaging models
Probably the best way to ensure robust inferences and estimate errors is to have multiple experimental replicates, ideally on different libraries.

Here we describe how to average model fits across libraries and/or replicates.

## Split data into replicates
We will use our data for the RBD as an earlier examples, but split it into several libraries / replicates.

Specifically, we will fit two different libraries: `avg2muts` and `avg3muts`, which have different barcodes and also different mutation rates (although of course in real life you might sometimes want to average results from different libraries with the same mutation rates).
We will also simulate having two replicates for each library just by sampling each library.
To make this example faster, we'll just use one concentration:

In [1]:
import pandas as pd

import polyclonal.polyclonal
import polyclonal.polyclonal_collection


# read data
all_data = pd.read_csv("RBD_variants_escape_noisy.csv", na_filter=None)

# split by library and replicates
libraries = ["avg2muts", "avg3muts"]  # the two libraries to use
concentrations = [1]  # use just use this concentration
n_replicates = 2  # number of replicates per library

data_by_replicate = {
    (library, replicate + 1): (
        all_data.query("library == @library")
        .query("concentration in @concentrations")
        .sample(frac=0.3, random_state=replicate)
    )
    for library in libraries
    for replicate in range(n_replicates)
}

## Fit models to each replicate
We now fit a `Polyclonal` model to each replicate using just 2 epitopes, as the data don't seem sufficient to accurately fit all three epitopes.
Then we arrange the models in a data frame:

In [2]:
# first create a data frame with all the models
models_by_replicate = {}
for (library, replicate), data in data_by_replicate.items():
    model = polyclonal.Polyclonal(data_to_fit=data, n_epitopes=2)
    models_by_replicate[(library, replicate)] = model
models_df = (
    pd.Series(models_by_replicate, name="model")
    .rename_axis(["library", "replicate"])
    .reset_index()
)

# now fit the models
n_fit, n_failed, models_df["model"] = polyclonal.polyclonal_collection.fit_models(
    models_df["model"],
    n_threads=2,
    reg_escape_weight=0.01,
    reg_uniqueness2_weight=0,
)

Note how the models are arranged in a data frame:

In [3]:
# NBVAL_IGNORE_OUTPUT

models_df

library  replicate                                              model
0  avg2muts          1  <polyclonal.polyclonal.Polyclonal object at 0x...
1  avg2muts          2  <polyclonal.polyclonal.Polyclonal object at 0x...
2  avg3muts          1  <polyclonal.polyclonal.Polyclonal object at 0x...
3  avg3muts          2  <polyclonal.polyclonal.Polyclonal object at 0x...

## Average the models
Now we create a `PolyclonalAverage` model with the models to average.
Note that by default the "average" used by `PolyclonalAverage` is the **median** rather than the **mean** between epitopes, although this is a parameter that can also be set to mean.

If your epitopes are too different or poorly defined (e.g., you are trying to fit more epitopes than can be consistently inferred from the data), then you may get an epitope harmonization error:

In [4]:
model_avg = polyclonal.PolyclonalAverage(models_df)

Let's look at the correlation among the escape at each epitope across models:

In [5]:
# NBVAL_IGNORE_OUTPUT

model_avg.mut_escape_corr_heatmap()

alt.Chart(...)

Look at the activities of the epitopes and the rest of the curves.
Note how a dark line is shown for the average, and thin lines for individual replicates.
It should generally be the case that the epitope with greater activity (more left shifted in plot below) should also be better correlated among replicates (heatmap above) as it can be inferred more reliably:

In [6]:
# NBVAL_IGNORE_OUTPUT

model_avg.curves_plot()

alt.Chart(...)

We can access the average escape values.
Note that there is also a column *escape_min_magnitude* that gives the lowest magnitude value:

In [7]:
# NBVAL_IGNORE_OUTPUT

model_avg.mut_escape_df

epitope  site wildtype mutant mutation  escape_mean  escape_median  \
0          1   331        N      A    N331A     0.048308      -0.052616   
1          1   331        N      D    N331D    -0.008830       0.033303   
2          1   331        N      E    N331E     0.046452      -0.034107   
3          1   331        N      F    N331F    -0.065502      -0.018698   
4          1   331        N      G    N331G    -0.009202      -0.006274   
...      ...   ...      ...    ...      ...          ...            ...   
3859       2   531        T      R    T531R    -0.049242      -0.057931   
3860       2   531        T      S    T531S     0.035896      -0.017057   
3861       2   531        T      V    T531V     0.147880       0.152604   
3862       2   531        T      W    T531W     0.085725       0.022115   
3863       2   531        T      Y    T531Y     0.137896       0.046106   

      escape_min_magnitude  escape_std  n_models  times_seen  frac_models  
0                -0.036304    0.192935         4       18.00          1.0  
1                -0.015432    0.164653         4       10.00          1.0  
2                -0.024267    0.235078         4        8.25          1.0  
3                 0.008263    0.296913         4        9.00          1.0  
4                -0.005629    0.075308         4       20.50          1.0  
...                    ...         ...       ...         ...          ...  
3859             -0.018060    0.062665         4       26.00          1.0  
3860             -0.006906    0.107428         4       32.00          1.0  
3861              0.008420    0.173945         4       17.50          1.0  
3862             -0.000988    0.125587         4        7.00          1.0  
3863              0.007967    0.202525         4       11.00          1.0  

[3864 rows x 12 columns]

We can do the same for the ICXX values:

In [8]:
# NBVAL_IGNORE_OUTPUT

model_avg.mut_icXX_df(
    x=0.9,
    icXX_col="IC90",
    log_fold_change_icXX_col="log2 fold change IC90",
)

site wildtype mutant  log2 fold change IC90 mean  \
0      331        N      A                   -0.098421   
1      331        N      D                    0.042379   
2      331        N      E                    0.034673   
3      331        N      F                   -0.117376   
4      331        N      G                   -0.010424   
...    ...      ...    ...                         ...   
2100   531        T      S                    0.109192   
2101   531        T      T                    0.000000   
2102   531        T      V                    0.201576   
2103   531        T      W                    0.110538   
2104   531        T      Y                    0.137844   

      log2 fold change IC90 median  log2 fold change IC90 min_magnitude  \
0                        -0.125117                            -0.023685   
1                         0.003701                             0.001566   
2                        -0.036331                            -0.009951   
3                        -0.139365                             0.000071   
4                        -0.062166                            -0.034888   
...                            ...                                  ...   
2100                      0.089153                            -0.029410   
2101                      0.000000                             0.000000   
2102                      0.207029                             0.002574   
2103                      0.025211                            -0.002463   
2104                      0.059015                             0.000108   

      log2 fold change IC90 std  n_models  times_seen  frac_models  
0                      0.240181         4       18.00          1.0  
1                      0.151895         4       10.00          1.0  
2                      0.160681         4        8.25          1.0  
3                      0.077196         4        9.00          1.0  
4                      0.141157         4       20.50          1.0  
...                         ...       ...         ...          ...  
2100                   0.149338         4       32.00          1.0  
2101                   0.000000         4         NaN          1.0  
2102                   0.143469         4       17.50          1.0  
2103                   0.170120         4        7.00          1.0  
2104                   0.187054         4       11.00          1.0  

[2105 rows x 10 columns]

Or the per-replicate escape values:

In [9]:
# NBVAL_IGNORE_OUTPUT

model_avg.mut_escape_df_replicates

epitope  site wildtype mutant mutation    escape  times_seen   library  \
0           1   331        N      A    N331A -0.036304          13  avg2muts   
1           1   331        N      D    N331D -0.270726           8  avg2muts   
2           1   331        N      E    N331E -0.043947           5  avg2muts   
3           1   331        N      F    N331F -0.526077           6  avg2muts   
4           1   331        N      G    N331G -0.006920          13  avg2muts   
...       ...   ...      ...    ...      ...       ...         ...       ...   
15431       2   531        T      R    T531R -0.018060          32  avg3muts   
15432       2   531        T      S    T531S  0.220646          39  avg3muts   
15433       2   531        T      V    T531V -0.056042          26  avg3muts   
15434       2   531        T      W    T531W  0.300722          11  avg3muts   
15435       2   531        T      Y    T531Y  0.084246           9  avg3muts   

       replicate  
0              1  
1              1  
2              1  
3              1  
4              1  
...          ...  
15431          2  
15432          2  
15433          2  
15434          2  
15435          2  

[15436 rows x 9 columns]

Now let's plot the escape.
See how you can select mutations based not only on how many times they are seen (averaged over all models in average), but also the number of models in which they are seen.

In [10]:
# NBVAL_IGNORE_OUTPUT

model_avg.mut_escape_plot(addtl_slider_stats={"times_seen": 2})

alt.VConcatChart(...)

Here is the same plot plotting the lowest magnitude escape value across libraries for each mutation:

In [11]:
# NBVAL_IGNORE_OUTPUT

model_avg.mut_escape_plot(
    addtl_slider_stats={"times_seen": 2}, avg_type="min_magnitude"
)

alt.VConcatChart(...)

We can also plot the log fold change in IC90 caused by each mutation:

In [12]:
# NBVAL_IGNORE_OUTPUT

model_avg.mut_icXX_plot(
    addtl_slider_stats={"times_seen": 2},
    avg_type="median",
)

alt.VConcatChart(...)

## Escape values by region
In some cases, you may want to only get the escape values for a specific region of the protein for each model being averaged.
For instance, this may be the case if you covered half the protein in one library and the other half in the other library.

In this case, you should initialize with a column in the models data with a `region_col` that specifies the sites for each model:

In [13]:
# assign all sites to the regions for the `avg2muts` library, but only
# some sites for the `avg3muts` library
regions_df = pd.DataFrame(
    [
        ("avg2muts", 1, model_avg.sites),
        ("avg2muts", 2, model_avg.sites),
        ("avg3muts", 1, [r for r in model_avg.sites if r <= 460]),
        ("avg3muts", 2, [r for r in model_avg.sites if r >= 450]),
    ],
    columns=["library", "replicate", "sites_to_keep"],
)

models_region_df = models_df.merge(regions_df)

print("Here is the input dataframe specifying sites to keep for each model:")
display(models_region_df)

model_region_avg = polyclonal.PolyclonalAverage(
    models_region_df, region_col="sites_to_keep"
)

Here is the input dataframe specifying sites to keep for each model:


library  replicate                                              model  \
0  avg2muts          1  <polyclonal.polyclonal.Polyclonal object at 0x...   
1  avg2muts          2  <polyclonal.polyclonal.Polyclonal object at 0x...   
2  avg3muts          1  <polyclonal.polyclonal.Polyclonal object at 0x...   
3  avg3muts          2  <polyclonal.polyclonal.Polyclonal object at 0x...   

                                       sites_to_keep  
0  (331, 332, 333, 334, 335, 336, 337, 338, 339, ...  
1  (331, 332, 333, 334, 335, 336, 337, 338, 339, ...  
2  [331, 332, 333, 334, 335, 336, 337, 338, 339, ...  
3  [450, 451, 452, 453, 455, 456, 458, 459, 460, ...

We can see the number of sites in each region:

In [14]:
for desc, sites in zip(model_region_avg.model_descriptors, model_region_avg.regions):
    print(f"{desc=}, {len(sites)=}, {min(sites)=}, {max(sites)=}")

desc={'library': 'avg2muts', 'replicate': 1}, len(sites)=173, min(sites)=331, max(sites)=531
desc={'library': 'avg2muts', 'replicate': 2}, len(sites)=173, min(sites)=331, max(sites)=531
desc={'library': 'avg3muts', 'replicate': 1}, len(sites)=112, min(sites)=331, max(sites)=460
desc={'library': 'avg3muts', 'replicate': 2}, len(sites)=70, min(sites)=450, max(sites)=531


We can also get the number of models per site.
Based on how we initialized, this is 3 for all sites except those between 450 and 460 where it is 4:

In [15]:
assert model_region_avg.sites == model_avg.sites

assert (
    model_region_avg.n_models_by_site[r] == 3 + (450 <= r <= 460)
    for r in model_region_avg.sites
)

Now look at the mutation-escape data frame:

In [16]:
# NBVAL_IGNORE_OUTPUT

model_region_avg.mut_escape_df

epitope  site wildtype mutant mutation  escape_mean  escape_median  \
0          1   331        N      A    N331A     0.091990      -0.036304   
1          1   331        N      D    N331D    -0.068040      -0.015432   
2          1   331        N      E    N331E     0.123654      -0.024267   
3          1   331        N      F    N331F    -0.187824      -0.045659   
4          1   331        N      G    N331G    -0.010393      -0.006920   
...      ...   ...      ...    ...      ...          ...            ...   
3859       2   531        T      R    T531R    -0.078201      -0.097801   
3860       2   531        T      S    T531S     0.050163      -0.027208   
3861       2   531        T      V    T531V     0.083055       0.008420   
3862       2   531        T      W    T531W     0.099228      -0.000988   
3863       2   531        T      Y    T531Y     0.023152       0.007967   

      escape_min_magnitude  escape_std  n_models  times_seen  frac_models  
0                -0.036304    0.204937         3   16.666667          1.0  
1                -0.015432    0.148742         3    9.333333          1.0  
2                -0.024267    0.223252         3    8.000000          1.0  
3                 0.008263    0.240191         3    7.666667          1.0  
4                -0.006920    0.086925         3   18.000000          1.0  
...                    ...         ...       ...         ...          ...  
3859             -0.018060    0.043376         3   25.333333          1.0  
3860             -0.027208    0.120721         3   29.000000          1.0  
3861              0.008420    0.153406         3   15.666667          1.0  
3862             -0.000988    0.142479         3    6.000000          1.0  
3863              0.007967    0.044984         3   10.000000          1.0  

[3864 rows x 12 columns]

For the sites where all four models are active, this will be the same as the model without regions:

In [17]:
assert (
    model_avg.mut_escape_df.query("(site >= 450) and (site <= 460)").equals(
        model_region_avg.mut_escape_df.query("(site >= 450) and (site <= 460)")
    )
    is True
)

But they differ at other sites:

In [18]:
assert model_avg.mut_escape_df.equals(model_region_avg.mut_escape_df) is False

Same for the mutation IC50 values:

In [19]:
# NBVAL_IGNORE_OUTPUT

region_ic50_df = model_region_avg.mut_icXX_df(
    x=0.5, icXX_col="IC50", log_fold_change_icXX_col="log_fold_change_IC50"
)

region_ic50_df

site wildtype mutant  log_fold_change_IC50 mean  \
0      331        N      A                  -0.091752   
1      331        N      D                   0.083860   
2      331        N      E                   0.023522   
3      331        N      F                  -0.064143   
4      331        N      G                   0.022005   
...    ...      ...    ...                        ...   
2100   531        T      S                   0.050891   
2101   531        T      T                   0.000000   
2102   531        T      V                   0.158352   
2103   531        T      W                   0.134829   
2104   531        T      Y                   0.033239   

      log_fold_change_IC50 median  log_fold_change_IC50 min_magnitude  \
0                       -0.018880                           -0.018880   
1                        0.011672                            0.011672   
2                       -0.062596                           -0.062596   
3                       -0.088000                           -0.002392   
4                       -0.039017                           -0.039017   
...                           ...                                 ...   
2100                    -0.040930                           -0.040930   
2101                     0.000000                            0.000000   
2102                     0.056386                            0.008097   
2103                    -0.002737                           -0.002737   
2104                     0.006375                            0.006375   

      log_fold_change_IC50 std  n_models  times_seen  frac_models  
0                     0.263594         3   16.666667          1.0  
1                     0.171600         3    9.333333          1.0  
2                     0.154679         3    8.000000          1.0  
3                     0.044039         3    7.666667          1.0  
4                     0.160212         3   18.000000          1.0  
...                        ...       ...         ...          ...  
2100                  0.134685         3   29.000000          1.0  
2101                  0.000000         3         NaN          1.0  
2102                  0.179433         3   15.666667          1.0  
2103                  0.196312         3    6.000000          1.0  
2104                  0.062134         3   10.000000          1.0  

[2105 rows x 10 columns]

In [20]:
ic50_df = model_avg.mut_icXX_df(
    x=0.5, icXX_col="IC50", log_fold_change_icXX_col="log_fold_change_IC50"
)

assert (
    region_ic50_df.query("(site >= 450) and (site <= 460)").equals(
        ic50_df.query("(site >= 450) and (site <= 460)")
    )
    is True
)

assert region_ic50_df.equals(ic50_df) is False

In [21]:
# NBVAL_IGNORE_OUTPUT

model_region_avg.mut_escape_plot(addtl_slider_stats={"times_seen": 2})

alt.VConcatChart(...)